In [356]:
###IMPORTS 
import re
import csv
import yahoo_fin.stock_info as YahooFin
import plotly.express as px
from tqdm import tqdm
import time
from scipy import stats 
from scipy import spatial
import json
import os
import numpy as np
import queue
import pandas as pd
from alpha_vantage.timeseries import TimeSeries
import time
import requests
from datetime import datetime, timedelta
import datetime
from plotly.offline import iplot
from sklearn.model_selection import train_test_split


Create a list of trading days 

In [357]:
###download AAPL to create a list of trading Days
def DownloadDailyData( ticker):
    api_key = "IZAJZ46QVQWRFAR4"
    ts = TimeSeries(key=api_key, output_format = 'pandas')

    data, metaData = ts.get_daily_adjusted(ticker,  outputsize = 'full')
    data.to_csv("appleDF.csv")
    data = pd.read_csv("appleDF.csv")
    return data

AAPLDF = DownloadDailyData("AAPL")
dateList = AAPLDF['date'].tolist()
dateList

In [359]:
## check to see if time in inbetween interval
def checkTimeInterval(time, sH=4,sM=0, eH=20,eM=0):
    return ((time.hour == sH and time.minute >= sM) or time.hour > sH) and ((time.hour == eH and time.minute <= eM) or time.hour < eH )
### grab a segment of mintute data
def stripData(path,date):
    

    dayOfMonth = str(date)[8:10]
    month = str(date)[5:7]
    year = str(date)[0:4]

    df = pd.read_csv(path)

    ##filter out selected Days 
    df['time'] = pd.to_datetime(df['time'],format='%Y-%m-%d %H:%M:%S')
    dateIndex = dateList.index(date)
    dayBeforeIndex = dateIndex+2
    date2 = dateList[dayBeforeIndex]
    dayOfMonth2 = str(date2)[8:10]
    month2 = str(date2)[5:7]
    year2 = str(date2)[0:4]
    
    candidates=['Unnamed: 0']
    df = df.drop([x for x in candidates if x in df.columns], axis=1)
    

    
    #### select times 
    timestamp1 = pd.Timestamp(int(year2), int(month2), int(dayOfMonth2), 9,30,0)
    timestamp2 = pd.Timestamp(int(year), int(month), int(dayOfMonth), 20,0,0)
    minutesBack = int(pd.Timedelta(timestamp2 - timestamp1).seconds / 60.0) + int(pd.Timedelta(timestamp2 - timestamp1).days *1440) 

    ###create dataframe with just the desired time interval
    timesList = [timestamp1 + datetime.timedelta(hours=nMin/60) for nMin in range(minutesBack)]
    d = df[(df['time'] > timestamp1)&(df['time'] < timestamp2)]
    d = d.sort_values('time')
    d['dollarVolume'] = d['volume']*d['close']
    valid = False
    
    ### create targets to train for deep learning
    targetC = d.loc[d['time'] == pd.Timestamp(int(year), int(month), int(dayOfMonth), 16 ,0,0), 'close'].to_list()
    targetO = d.loc[d['time'] == pd.Timestamp(int(year), int(month), int(dayOfMonth), 9 ,31,0), 'open'].to_list()
    if len(targetC) !=0 and len(targetO):
        target = (targetC[0] - targetO[0])/targetO[0]
        d['target'] = target
        valid = True
    else:
        
        return d, False
        
        
    ###clean the data by filling in holes
    cp = float(d['open'].head(1))
    vp =float(d['volume'].head(1))
    dv = float(d['dollarVolume'].head(1))
    d.set_index('time')
    d_dict = d.to_dict('reccords')
    dd_dict = {}
    columns=['time','open','high','low','close','volume','target','dollarVolume']
    
    for row in d_dict:
        key = row['time']
        dd_dict[key] = row
    
    rowsAdded = 0
    cleanedD = pd.DataFrame(columns=columns)
    dfList = []

    for key in timesList:
        if checkTimeInterval(key, 4, 0, 19, 59) and str(key.date()) in dateList: 
            try:
                
                t,o,h,l,c,v,t, dv = list(dd_dict[key].values())
                values=[key, (o-cp)/cp,(h-cp)/cp,(l-cp)/cp,(c-cp)/cp,(v-vp)/vp,target, dv]
                newRow = pd.DataFrame(dict(zip(columns,values)),index=[0])
                dfList.append(newRow)
                cp = dd_dict[key]['close'] 
                vp = dd_dict[key]['volume']
            except (KeyError, ZeroDivisionError): 
                values=[key, 0, 0, 0, 0, 0,target,0]
                newRow = pd.DataFrame(dict(zip(columns,values)),index=[0])
                dfList.append(newRow)
                rowsAdded+=1

    d = pd.concat(dfList)
    d = d.sort_values('time')

    ###Strip additional information for training
    
    d['month'] = np.sin(d['time'].dt.month*np.pi/12)
    d['year'] = d['time'].dt.year
    d['day'] = np.sin(d['time'].dt.day*np.pi/31)
    
    ###for minutes Make it based on minutes since 4:00 AM and sin wave it to 20:00
    d['minuteSin '] = np.sin((d['time' ].dt.hour*60 + d['time'].dt.minute - 4.00*60)*np.pi/(60*16))
    d['minute'] = d['time' ].dt.hour*60 + d['time'].dt.minute

    
    return d, valid

SELECT MINUTELY STOCKS 

In [360]:
dfs = pd.read_pickle("DailyAnalysis/StockDataSet.pkl")

In [362]:
###load sample stocks
dfTrades_list = []
for name, group in dfs.groupby(['symbol']):
    group['averageVolume'] = group['dollarVolume'].mean()
    dfTrades_list.append(group)
dfs = pd.concat(dfTrades_list)

In [363]:
dfs = dfs[dfs['close1'] > 1]
dfs = dfs[dfs['open'] > .5]

CALCULATE SD OF STOCK 

In [364]:
### HIGH DOLLAR VOLUME STOCKS 
dfs_HV_list = []
for name, group in dfs.groupby(['datetime']):
    dfs_HV_list.append(group.sort_values(by='premarket_gain', ascending=False).head(10))
dfs_HV = pd.concat(dfs_HV_list).sort_values(['datetime'])


In [365]:
dfTradeDays = dfs_HV.copy()

In [366]:
dfTradeDays[dfTradeDays['close']<0]

Empty DataFrame
Columns: [datetime, open, high, low, close, 5. adjusted close, volume, 8. split coefficient, symbol, splitRatio, pct_gain, premarket_gain1, premarket_gain, premarket_gainN, dayGain, dayGain1, day1volume, pct_gain1, close1, 6day_change, 5day_change, dayGainN, dollarVolume, averageVolume]
Index: []

[0 rows x 24 columns]

In [367]:
### validate all dataframes are the same length 
for df in IntradayData.values():
    print(df[df['dollarVolume'] <0])
    if len(df) != 2550: print(len(df))

Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
                  time      open      high       low     close    volume  \
0  2020-02-04 04:01:00  0.000000  0.006268  0.000000  0.001343  0.000000   
0  2020-02-04 04:02:00  0.011923  0.014903  0.011923  0.014903 -0.019644   
0  2020-02-04 04:03:00  0.002349  0.016006  0.002349  0.016006  0.959546   
0  2020-02-04 04:04:00 -0.004480  0.010117 -0.004480  0.004480 -0.439514   
0  2020-02-04 04:05:00  0.000144  0.002446 -0.015827  0.000000 -0.614802   
..                 ...       ...       ...       ...       ...       ...   
0  2020-02-04 19:55:00  0.000000  0.000150  0.000000  0.000150 -0.561538   
0  2020-02-04 19:56:00  0.000300  0.000300  0.000000  0.000000  0.710526   
0  2020-02-04 19:57:00 -0.002100 -0.002100 -0.00

                  time      open      high       low     close    volume  \
0  2020-02-05 04:03:00  0.000000  0.000000 -0.001657 -0.001657  0.000000   
0  2020-02-05 04:04:00  0.002466  0.002466  0.002466  0.002466 -0.754367   
0  2020-02-05 04:06:00  0.000142  0.000142  0.000142  0.000142 -0.555556   
0  2020-02-05 04:07:00 -0.000710 -0.000710 -0.000710 -0.000710  0.050000   
0  2020-02-05 04:09:00  0.000047  0.000047  0.000047  0.000047  1.400000   
..                 ...       ...       ...       ...       ...       ...   
0  2020-02-05 19:33:00  0.000048  0.000048  0.000048  0.000048 -0.945455   
0  2020-02-05 19:42:00  0.000476  0.000714  0.000476  0.000714  5.000000   
0  2020-02-05 19:43:00  0.000000  0.000999  0.000000  0.000999  0.573333   
0  2020-02-05 19:57:00 -0.000761 -0.000285 -0.000761 -0.000285 -0.578390   
0  2020-02-05 19:59:00 -0.000476 -0.000476 -0.000476 -0.000476 -0.631491   

      target  dollarVolume  month  year       day  minuteSin   minute  
0  -0.010729   

Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
                  time      open      high       low     close    volume  \
0  2020-02-06 09:31:00  0.000000  0.000594 -0.004310 -0.002972  0.000000   
0  2020-02-06 09:32:00 -0.000075 -0.000075 -

                  time      open      high       low     close    volume  \
0  2020-02-07 09:31:00  0.000000  0.001049 -0.001251  0.000258  0.000000   
0  2020-02-07 09:32:00  0.000018  0.002552 -0.000282  0.002232 -0.827278   
0  2020-02-07 09:33:00 -0.000166  0.000188 -0.001075 -0.001075 -0.244935   
0  2020-02-07 09:34:00  0.000137  0.000239 -0.001503 -0.000156  1.380876   
0  2020-02-07 09:35:00  0.000034  0.000851 -0.000252 -0.000191 -0.325962   
..                 ...       ...       ...       ...       ...       ...   
0  2020-02-11 16:29:00 -0.000013 -0.000013 -0.000013 -0.000013 -0.649123   
0  2020-02-11 16:30:00 -0.000417 -0.000417 -0.000417 -0.000417  0.500000   
0  2020-02-11 16:31:00 -0.000026 -0.000026 -0.000026 -0.000026 -0.303333   
0  2020-02-11 16:34:00  0.000026  0.000026  0.000026  0.000026  0.990431   
0  2020-02-11 16:45:00 -0.000291 -0.000291 -0.000291 -0.000291  1.218750   

      target  dollarVolume  month  year       day  minuteSin   minute  
0  -0.002062   

Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
Empty DataFrame
Columns: [time, open, high, low, close, volume, target, dollarVolume, month, year, day, minuteSin , minute]
Index: []
                  time      open      high       low     close    volume  \
0  2020-02-11 09:31:00  0.000000  0.001680 -0.001103  0.000789  0.000000   
0  2020-02-11 09:32:00  0.000772  0.003762 -0.000930  0.003762 -0.714147   
0  2020-02-11 09:33:00  0.000000  0.004150 -0.000113  0.001289  0.575915   
0  2020-02-11 09:34:00  0.000594  0.002052 -0.000523  0.000101 -0.739964   
0  2020-02-11 09:35:00 -0.000223 -0.000223 -0.015835 -0.015835  3.346520   
..                 ...       ...       ...       ...       ...       ...   
0  2020-02-13 18:48:00 -0.000935 -0.000935 -0.000935 -0.000935 -0.

...

                  time      open      high       low     close    volume  \
0  2021-12-09 09:31:00  0.000000  0.002149 -0.009884 -0.008810  0.000000   
0  2021-12-09 09:32:00 -0.000867  0.005784 -0.005853  0.004652 -0.475788   
0  2021-12-09 09:33:00 -0.000099  0.000764 -0.005709 -0.003983 -0.453830   
0  2021-12-09 09:34:00 -0.000065  0.001399 -0.006499  0.000867  0.836471   
0  2021-12-09 09:35:00 -0.000433  0.000866 -0.001299 -0.000433 -0.536547   
..                 ...       ...       ...       ...       ...       ...   
0  2021-12-13 19:42:00  0.000000  0.000000  0.000000  0.000000  1.010050   
0  2021-12-13 19:43:00  0.000000  0.000000  0.000000  0.000000  0.550000   
0  2021-12-13 19:47:00  0.001015  0.001015  0.001015  0.001015 -0.838710   
0  2021-12-13 19:52:00  0.000000  0.000000  0.000000  0.000000  0.530000   
0  2021-12-13 19:56:00  0.001014  0.001014  0.001014  0.001014 -0.346405   

      target  dollarVolume         month  year       day  minuteSin   minute  
0  -0.00

                  time      open      high       low     close    volume  \
0  2021-12-13 09:31:00  0.000000  0.000200 -0.001597 -0.000798  0.000000   
0  2021-12-13 09:32:00  0.000000  0.001598  0.000000  0.000999 -0.824828   
0  2021-12-13 09:33:00 -0.000100  0.001397 -0.000100  0.000299 -0.220608   
0  2021-12-13 09:34:00  0.000000  0.001297 -0.001397 -0.000499  0.326188   
0  2021-12-13 09:35:00  0.000100  0.000699 -0.000998 -0.000798 -0.241163   
..                 ...       ...       ...       ...       ...       ...   
0  2021-12-15 19:46:00 -0.000593 -0.000593 -0.000593 -0.000593  3.460000   
0  2021-12-15 19:47:00 -0.000198 -0.000198 -0.000198 -0.000198 -0.578475   
0  2021-12-15 19:51:00  0.000593  0.000593  0.000593  0.000593 -0.468085   
0  2021-12-15 19:56:00 -0.000395 -0.000395 -0.000395 -0.000395  0.300000   
0  2021-12-15 19:59:00  0.000593  0.000593  0.000593  0.000593  1.007692   

      target  dollarVolume         month  year       day  minuteSin   minute  
0  -0.00

                  time      open      high       low     close    volume  \
0  2021-12-14 09:31:00  0.000000  0.000263 -0.019494 -0.012118  0.000000   
0  2021-12-14 09:32:00 -0.002859  0.020533 -0.002859  0.017867 -0.623361   
0  2021-12-14 09:33:00  0.000262  0.005237 -0.004978  0.001048  0.201785   
0  2021-12-14 09:34:00 -0.000785  0.002094 -0.010468 -0.009945  0.002603   
0  2021-12-14 09:35:00  0.000000  0.002247 -0.003436  0.001057 -0.163729   
..                 ...       ...       ...       ...       ...       ...   
0  2021-12-16 19:54:00  0.000003  0.002036  0.000000  0.002036  0.983910   
0  2021-12-16 19:56:00 -0.001778 -0.001778 -0.001778 -0.001778 -0.841038   
0  2021-12-16 19:57:00  0.001018  0.001526  0.001018  0.001526  1.147959   
0  2021-12-16 19:58:00  0.000000  0.000000 -0.000508  0.000000  2.735154   
0  2021-12-16 19:59:00 -0.000254 -0.000254 -0.000508 -0.000254 -0.737361   

      target  dollarVolume         month  year       day  minuteSin   minute  
0  -0.02

                  time      open      high       low     close    volume  \
0  2021-12-16 09:31:00  0.000000  0.011925 -0.000243  0.007072  0.000000   
0  2021-12-16 09:32:00  0.001677  0.005783 -0.001948  0.003920 -0.491000   
0  2021-12-16 09:33:00  0.000173  0.000895 -0.011862 -0.009937 -0.186570   
0  2021-12-16 09:34:00  0.001028  0.001459 -0.009482 -0.008510  0.644009   
0  2021-12-16 09:35:00  0.000000  0.010299 -0.000228  0.009809 -0.453396   
..                 ...       ...       ...       ...       ...       ...   
0  2021-12-20 19:53:00  0.000000  0.000000  0.000000  0.000000 -0.834532   
0  2021-12-20 19:55:00 -0.000790  0.000000 -0.000790 -0.000003  6.313043   
0  2021-12-20 19:56:00 -0.001314 -0.001314 -0.001314 -0.001314 -0.738407   
0  2021-12-20 19:58:00  0.000791  0.000791  0.000791  0.000791  1.554545   
0  2021-12-20 19:59:00 -0.000790  0.000790 -0.000790  0.000790  3.188612   

      target  dollarVolume         month  year       day  minuteSin   minute  
0  -0.00

                  time      open      high       low     close    volume  \
0  2021-12-20 09:31:00  0.000000  0.006223 -0.003586  0.001570  0.000000   
0  2021-12-20 09:32:00 -0.001462  0.006016 -0.002620  0.003488 -0.807322   
0  2021-12-20 09:33:00  0.000000  0.009026 -0.002938  0.005930 -0.070246   
0  2021-12-20 09:34:00 -0.001382  0.001200 -0.014033 -0.004539  0.567654   
0  2021-12-20 09:35:00 -0.002620  0.010376 -0.006392  0.007756 -0.338173   
..                 ...       ...       ...       ...       ...       ...   
0  2021-12-22 19:08:00 -0.000730 -0.000730 -0.000730 -0.000730  0.859903   
0  2021-12-22 19:14:00 -0.002503 -0.002503 -0.002503 -0.002503 -0.277922   
0  2021-12-22 19:18:00 -0.000837 -0.000837 -0.000837 -0.000837  2.597122   
0  2021-12-22 19:35:00  0.004082  0.004082  0.004082  0.004082 -0.750000   
0  2021-12-22 19:59:00 -0.002502 -0.002502 -0.003023 -0.003023  2.244000   

      target  dollarVolume         month  year       day  minuteSin   minute  
0  -0.00

In [368]:
dfTradeDays =dfTradeDays[dfTradeDays['datetime'] > pd.Timestamp(2020,2,3)]

In [369]:
d_dict = dfTradeDays.to_dict('records')

In [370]:
IntradayData['RIVN2021-12-22']

time      open      high       low     close    volume  \
0  2021-12-20 09:30:00  0.000000  0.000000  0.000000  0.000000  0.000000   
0  2021-12-20 09:31:00  0.000000  0.006223 -0.003586  0.001570  0.000000   
0  2021-12-20 09:32:00 -0.001462  0.006016 -0.002620  0.003488 -0.807322   
0  2021-12-20 09:33:00  0.000000  0.009026 -0.002938  0.005930 -0.070246   
0  2021-12-20 09:34:00 -0.001382  0.001200 -0.014033 -0.004539  0.567654   
..                 ...       ...       ...       ...       ...       ...   
0  2021-12-22 19:55:00  0.000000  0.000000  0.000000  0.000000  0.000000   
0  2021-12-22 19:56:00  0.000000  0.000000  0.000000  0.000000  0.000000   
0  2021-12-22 19:57:00  0.000000  0.000000  0.000000  0.000000  0.000000   
0  2021-12-22 19:58:00  0.000000  0.000000  0.000000  0.000000  0.000000   
0  2021-12-22 19:59:00 -0.002502 -0.002502 -0.003023 -0.003023  2.244000   

      target  dollarVolume         month  year       day  minuteSin   minute  
0  -0.000701      0.000000  1.224647e-16  2021  0.897805    0.881921     570  
0  -0.000701     -0.000701  1.224647e-16  2021  0.897805    0.883459     571  
0  -0.000701     -0.000701  1.224647e-16  2021  0.897805    0.884988     572  
0  -0.000701     -0.000701  1.224647e-16  2021  0.897805    0.886507     573  
0  -0.000701     -0.000701  1.224647e-16  2021  0.897805    0.888016     574  
..       ...           ...           ...   ...       ...         ...     ...  
0  -0.000701      0.000000  1.224647e-16  2021  0.790776    0.016362    1195  
0  -0.000701      0.000000  1.224647e-16  2021  0.790776    0.013090    1196  
0  -0.000701      0.000000  1.224647e-16  2021  0.790776    0.009817    1197  
0  -0.000701      0.000000  1.224647e-16  2021  0.790776    0.006545    1198  
0  -0.000701     -0.000701  1.224647e-16  2021  0.790776    0.003272    1199  

[2550 rows x 13 columns]

In [371]:
IntradayData = {}
from pathlib import Path
### Clean the Data
for row in tqdm(d_dict):
    path = '/Users/sean/MinuteDataAllStocks/' + row['symbol'] + '.csv'
    if Path(path).is_file():
        date = str(row['datetime'].date())

        df, valid = stripData(path, date)
        filename = row['symbol'] + date
        if valid: 
            IntradayData[filename] = (df)
            print('worked')
            print(filename)
        else:
            print('failed')
            print(filename)
            
            


  0%|          | 1/4770 [00:00<52:18,  1.52it/s]

failed
MOXC2020-02-04


  0%|          | 2/4770 [00:01<54:20,  1.46it/s]

failed
TSLA2020-02-04
failed
DLA2020-02-04


  0%|          | 5/4770 [00:01<34:02,  2.33it/s]

...

worked
BTTR2021-12-22


100%|█████████▉| 4769/4770 [4:10:06<00:03,  3.45s/it]

worked
MYO2021-12-22


100%|██████████| 4770/4770 [4:10:10<00:00,  3.15s/it]

worked
MRAI2021-12-22


In [372]:
%%time
### turn dates into time stamps
for key in IntradayData:
    IntradayData[key]['time'] = pd.to_datetime(IntradayData[key]['time'],format='%Y-%m-%d %H:%M:%S')
    IntradayData[key] = IntradayData[key].sort_values(['time'])
    print(key)

GLMD2020-02-04
ALLT2020-02-04
ABUS2020-02-05
WWR2020-02-05
CODA2020-02-05
MHH2020-02-05
GHL2020-02-05
UIS2020-02-06
STIM2020-02-06
POAI2020-02-06
SRDX2020-02-06
PLIN2020-02-06
SYNA2020-02-07
BILL2020-02-07
SEED2020-02-10
ASTC2020-02-10
TMUS2020-02-11
ASTC2020-02-11
AMKR2020-02-11
ALNA2020-02-12
NURO2020-02-12
NTWK2020-02-12
SHOP2020-02-12
WORX2020-02-13
NNVC2020-02-13
APT2020-02-13
CPAH2020-02-13
BTAI2020-02-13
IMGN2020-02-14
BLNK2020-02-14
EXPE2020-02-14
BTAI2020-02-14
CGC2020-02-14
CEVA2020-02-18
MITO2020-02-18
BLPH2020-02-18
WSG2020-02-18
SMIT2020-02-19
HCKT2020-02-19
QUAD2020-02-19
SSTI2020-02-19
BBI2020-02-20
DPZ2020-02-20
ZG2020-02-20
AIRG2020-02-21
SFM2020-02-21
AERI2020-02-21
DBX2020-02-21
BXRX2020-02-21
EHTH2020-02-21
AVDL2020-02-21
VIR2020-02-24
NNVC2020-02-24
NGM2020-02-24
ENLV2020-02-24
APT2020-02-24
CJJD2020-02-24
CODX2020-02-24
LAKE2020-02-24
GMLP2020-02-25
ENDP2020-02-25
MRNA2020-02-25
NIO2020-02-25
LL2020-02-25
COCP2020-02-25
NLS2020-02-25
QRTEA2020-02-26
ALC2020-02-26


TH2020-05-28
AXLA2020-05-28
SMTC2020-05-28
ABIO2020-05-28
TGI2020-05-28
PHAS2020-05-28
CVU2020-05-28
MEIP2020-05-29
GNUS2020-05-29
MTC2020-05-29
TCON2020-05-29
ZS2020-05-29
TRIL2020-05-29
CHCI2020-05-29
ADAP2020-05-29
PHIO2020-05-29
SNOA2020-05-29
NTLA2020-06-01
LIND2020-06-01
VTSI2020-06-01
NERV2020-06-01
KLDO2020-06-01
SRTS2020-06-01
SWBI2020-06-01
AESE2020-06-01
DGLY2020-06-01
GNUS2020-06-01
RUHN2020-06-02
WU2020-06-02
IDRA2020-06-02
RIOT2020-06-02
GNUS2020-06-02
ALNA2020-06-02
TENX2020-06-02
WWR2020-06-02
MGI2020-06-02
AZUL2020-06-03
CAAP2020-06-03
ERJ2020-06-03
APPS2020-06-03
SAVA2020-06-03
GNUS2020-06-03
WISA2020-06-03
SECO2020-06-03
SCWX2020-06-04
ZUO2020-06-04
GNUS2020-06-04
SAVE2020-06-04
MREO2020-06-04
KZR2020-06-04
CIDM2020-06-04
UAL2020-06-05
AAL2020-06-05
RIG2020-06-05
WMC2020-06-05
MFA2020-06-05
IVR2020-06-05
MITT2020-06-05
XSPA2020-06-05
MCEP2020-06-05
QEP2020-06-08
IVR2020-06-08
MXC2020-06-08
CEI2020-06-08
MIK2020-06-08
FTSI2020-06-08
DGLY2020-06-08
SPCB2020-06-08
ENOB2

DKNG2020-09-02
NNOX2020-09-02
ETTX2020-09-02
AMC2020-09-02
VRA2020-09-02
GES2020-09-02
NVAX2020-09-03
DLTH2020-09-03
FIVE2020-09-03
AGTC2020-09-03
FGEN2020-09-03
FLGT2020-09-03
PHX2020-09-03
NX2020-09-04
ANPC2020-09-04
DOMO2020-09-04
LMPX2020-09-04
PLM2020-09-04
IMAB2020-09-04
BWMX2020-09-08
VXRT2020-09-08
SRAX2020-09-08
KMDA2020-09-08
CVV2020-09-08
MICT2020-09-08
NKLA2020-09-08
ALBO2020-09-08
TIGO2020-09-09
SCWX2020-09-09
NNOX2020-09-09
XTLB2020-09-09
IBIO2020-09-09
ASTC2020-09-09
AMYT2020-09-09
TRIL2020-09-09
ITCI2020-09-09
WTRE2020-09-09
DMTK2020-09-10
VRNT2020-09-10
MD2020-09-10
CRVS2020-09-10
OSTK2020-09-10
SLQT2020-09-10
YTEN2020-09-10
RH2020-09-10
VRTU2020-09-10
NES2020-09-11
MICT2020-09-11
PTON2020-09-11
DQ2020-09-11
ZUMZ2020-09-11
AMRK2020-09-11
LAUR2020-09-11
TAOP2020-09-11
BFRA2020-09-11
GENE2020-09-11
GME2020-09-14
PXLW2020-09-14
ETNB2020-09-14
MRSN2020-09-14
SGMS2020-09-14
SAVA2020-09-14
VXRT2020-09-14
LEU2020-09-15
IMRN2020-09-15
ELA2020-09-15
RLGT2020-09-15
PSTV2020-09-1

PBLA2020-12-10
GLSI2020-12-10
IMMP2020-12-10
HPK2020-12-11
TPGY2020-12-11
SNOA2020-12-11
VTVT2020-12-11
FRSX2020-12-11
FAT2020-12-11
LXRX2020-12-11
ZDGE2020-12-11
REPH2020-12-14
SYTA2020-12-14
ANIX2020-12-14
ALXN2020-12-14
ARVN2020-12-14
SYBX2020-12-14
VERU2020-12-14
ANPC2020-12-14
VTVT2020-12-15
VERU2020-12-15
MCEP2020-12-15
AVXL2020-12-15
AIV2020-12-15
OCX2020-12-15
PRVL2020-12-15
ACY2020-12-15
MARA2020-12-16
NBSE2020-12-16
CLLS2020-12-16
HTBX2020-12-16
AEMD2020-12-16
MIND2020-12-16
SIOX2020-12-16
TLRY2020-12-16
DTEA2020-12-16
MARA2020-12-17
BLBD2020-12-17
ABUS2020-12-17
BTBT2020-12-17
RAD2020-12-17
GB2020-12-17
CNSP2020-12-17
EOLS2020-12-17
DMTK2020-12-18
SNOA2020-12-18
MDNA2020-12-18
MDWD2020-12-18
MREO2020-12-18
SQFT2020-12-18
CNSP2020-12-18
CYTH2020-12-18
CURO2020-12-18
AIM2020-12-21
AJRD2020-12-21
CURI2020-12-21
RP2020-12-21
CCRC2020-12-21
NES2020-12-21
AGIO2020-12-21
ELYS2020-12-22
HUSN2020-12-22
EQOS2020-12-22
UAVS2020-12-22
SPWH2020-12-22
AMTX2020-12-22
JG2020-12-22
KLDO2020-

HOTH2021-03-23
DLPN2021-03-23
BNTC2021-03-23
BLFS2021-03-23
PLBY2021-03-24
BBIG2021-03-24
BCLI2021-03-24
AUVI2021-03-24
SOS2021-03-24
ALYA2021-03-24
APTO2021-03-24
DLPN2021-03-24
HOFV2021-03-24
ZKIN2021-03-24
PIRS2021-03-25
SSNT2021-03-25
ENOB2021-03-25
IMMP2021-03-25
HWCC2021-03-25
FSTX2021-03-25
AWH2021-03-26
LAIX2021-03-26
CLEU2021-03-26
TLS2021-03-26
NEXT2021-03-26
MX2021-03-26
ATNF2021-03-26
WAFU2021-03-26
BSMX2021-03-26
AGFS2021-03-29
SXTC2021-03-29
WKEY2021-03-29
DLPN2021-03-29
HMHC2021-03-29
FLY2021-03-29
CYAN2021-03-29
HGEN2021-03-29
SWAV2021-03-30
TLSA2021-03-30
ABCL2021-03-30
MNPR2021-03-30
CMPI2021-03-30
BIOC2021-03-30
YMAB2021-03-30
VTSI2021-03-30
CSCW2021-03-30
MBRX2021-03-30
CHWY2021-03-31
OCGN2021-03-31
PRPH2021-03-31
SURF2021-03-31
ELDN2021-03-31
CLRO2021-03-31
TAOP2021-03-31
RKDA2021-03-31
YVR2021-03-31
IDEX2021-04-01
QS2021-04-01
UAVS2021-04-01
PFIN2021-04-01
ACY2021-04-01
JAGX2021-04-01
FTFT2021-04-01
UPC2021-04-01
SNOA2021-04-01
FGF2021-04-05
OCUP2021-04-05
VVOS202

PIRS2021-06-25
NKE2021-06-25
RZLT2021-06-25
FFHL2021-06-25
OSMT2021-06-25
SPCE2021-06-25
VERV2021-06-28
AVXL2021-06-28
BEAM2021-06-28
EDIT2021-06-28
QADA2021-06-28
SNR2021-06-28
MRIN2021-06-28
RSLS2021-06-28
NTLA2021-06-28
CERE2021-06-29
BSQR2021-06-29
XELA2021-06-29
CNSP2021-06-29
AUUD2021-06-29
MRIN2021-06-29
DBGI2021-06-29
ORPH2021-06-29
EPAC2021-06-29
UPC2021-06-29
OCUP2021-06-30
HCM2021-06-30
SLS2021-06-30
STRM2021-06-30
BLIN2021-06-30
DXYN2021-06-30
ASTS2021-06-30
VTNR2021-06-30
XELA2021-06-30
KTRA2021-07-01
MRIN2021-07-01
SEEL2021-07-01
TTSH2021-07-01
SPRO2021-07-01
BGI2021-07-01
BLIN2021-07-01
ATHE2021-07-01
WNW2021-07-01
CRNC2021-07-02
NSYS2021-07-02
IDT2021-07-02
SPCE2021-07-02
BSQR2021-07-02
OSG2021-07-02
ALEC2021-07-02
MRIN2021-07-02
TATT2021-07-02
STAF2021-07-02
LRMR2021-07-06
ODT2021-07-06
ALXO2021-07-06
AXLA2021-07-06
BSQR2021-07-06
MRIN2021-07-06
BLIN2021-07-06
OSAT2021-07-06
PFSW2021-07-06
SALM2021-07-07
MAPS2021-07-07
MINM2021-07-07
BHVN2021-07-07
PFMT2021-07-07
ONCS2

NGS2021-09-28
CXDO2021-09-28
CRKN2021-09-28
ALF2021-09-28
FEIM2021-09-28
GOGO2021-09-28
EQOS2021-09-28
DBGI2021-09-28
ZIVO2021-09-28
SNOA2021-09-28
JZXN2021-09-29
FOLD2021-09-29
NFGC2021-09-29
PRQR2021-09-29
FBIO2021-09-29
AUVI2021-09-29
NCNA2021-09-29
GOVX2021-09-29
GREE2021-09-29
CLEU2021-09-30
PALT2021-09-30
OG2021-09-30
CEI2021-09-30
PRGO2021-09-30
BLIN2021-09-30
RGC2021-09-30
AMTX2021-09-30
OPRX2021-09-30
DATS2021-09-30
BTCM2021-10-01
SPWR2021-10-01
RIDE2021-10-01
BITF2021-10-01
AVIR2021-10-01
PALT2021-10-01
CDXS2021-10-01
BMRA2021-10-01
NEO2021-10-01
VEV2021-10-04
ADVM2021-10-04
RDHL2021-10-04
OPGN2021-10-04
ESBK2021-10-04
XENE2021-10-04
OTMO2021-10-04
DCTH2021-10-05
SNPX2021-10-05
SDPI2021-10-05
LGHL2021-10-05
AGFY2021-10-05
USEG2021-10-05
MARPS2021-10-05
TISI2021-10-05
PLTR2021-10-06
VYGR2021-10-06
BTBT2021-10-06
NRBO2021-10-06
ACER2021-10-06
LMFA2021-10-06
AYI2021-10-06
MOLN2021-10-06
DATS2021-10-07
TTM2021-10-07
RKLB2021-10-07
JAN2021-10-07
PFMT2021-10-07
NFE2021-10-07
MRUS20

In [342]:
#### itterate through minutly data and record the percetage of each trade into a PD dataframe

In [373]:
len(IntradayData)

3904

In [376]:
folderName = 'PreMarketGainStocks'
##export data to 
for key in tqdm(IntradayData):
    d = IntradayData[key]
    d.to_csv(folderName + '/'+key + ".csv")


100%|██████████| 3904/3904 [04:19<00:00, 15.02it/s]
